# Test of F12 matrix elements

## Initialization

In [5]:
let png_image = print_endline ;;

(* --------- *)

#cd "/home/scemama/QCaml";;
#use "topfind";;
#require "jupyter.notebook";;

let png_image name = 
    Jupyter_notebook.display_file ~base64:true "image/png" ("Notebooks/images/"^name)
;;

#require "lacaml.top";;
#require "alcotest";;
#require "str";;
#require "bigarray";;
#require "zarith";;
#require "getopt";;
#directory "_build";;
#directory "_build/Basis";;
#directory "_build/CI";;
#directory "_build/MOBasis";;
#directory "_build/Nuclei";;
#directory "_build/Parallel";;
#directory "_build/Perturbation";;
#directory "_build/SCF";;
#directory "_build/Utils";;

val png_image : string -> unit = <fun>


- : unit = ()
Findlib has been successfully loaded. Additional directives:
  #require "package";;      to load a package
  #list;;                   to list the available packages
  #camlp4o;;                to load camlp4 (standard syntax)
  #camlp4r;;                to load camlp4 (revised syntax)
  #predicates "p,q,...";;   to set these predicates
  Topfind.reset();;         to force that packages will be reloaded
  #thread;;                 to enable threads

- : unit = ()


val png_image : string -> Jupyter_notebook.display_id = <fun>


### Modules

In [6]:
#load "Constants.cmo";;
#load_rec "Util.cma";;
#load_rec "Matrix.cmo";;
#load_rec "Simulation.cmo";;
#load_rec "Spindeterminant.cmo";;
#load_rec "Determinant.cmo";;
#load_rec "HartreeFock.cmo";;
#load_rec "MOBasis.cmo";;
#load_rec "F12CI.cmo";;

### Printers

In [7]:
#install_printer AngularMomentum.pp_string ;;
#install_printer Basis.pp ;;
#install_printer Charge.pp ;;
#install_printer Coordinate.pp ;;
#install_printer Vector.pp;;
#install_printer Matrix.pp;;
#install_printer Util.pp_float_2darray;;
#install_printer Util.pp_float_array;;
#install_printer Util.pp_matrix;;
#install_printer HartreeFock.pp ;;
#install_printer Fock.pp ;;
#install_printer MOClass.pp ;;
let pp_mo ppf t = MOBasis.pp ~start:1 ~finish:0 ppf t ;;
#install_printer pp_mo;;
(*
#install_printer DeterminantSpace.pp;;
*)
#install_printer SpindeterminantSpace.pp;;
#install_printer Bitstring.pp;;

(* --------- *)

open Lacaml.D


val pp_mo : Format.formatter -> MOBasis.t -> unit = <fun>


## Run

### Simulation


In [10]:
let basis_filename  = "/home/scemama/qp2/data/basis/6-31g" 
let aux_basis_filename = "/home/scemama/qp2/data/basis/cc-pvdz" 
let nuclei = Nuclei.of_zmt_string "c" 
let frozen_core = false
let multiplicity = 1
let state = 1

let f12 = F12factor.gaussian_geminal 1.0 
let basis =  Basis.of_nuclei_and_basis_filenames ~f12 ~nuclei [basis_filename] 
let aux_basis =  Basis.of_nuclei_and_basis_filenames ~nuclei (basis_filename :: aux_basis_filename :: []) 
let charge = 0 


let simulation =
    Simulation.make 
        ~charge ~multiplicity ~nuclei
        ~cartesian:true
        basis


val basis_filename : string = "/home/scemama/qp2/data/basis/6-31g"


val aux_basis_filename : string = "/home/scemama/qp2/data/basis/cc-pvdz"


val nuclei : Nuclei.t = [|(Element.C,   0.0000   0.0000   0.0000)|]


val frozen_core : bool = false


val multiplicity : int = 1


...

val f12 : F12factor.t =
  {F12factor.expo_s = 1.;
   gaussian =
    {GaussianOperator.coef_g =
      [  -0.314400  -0.303700  -0.168100  -0.098110  -0.060240  -0.037260 ];
     expo_g =
      [   0.220900   1.004000   3.622000  12.160000  45.870000 254.400000 ];
     expo_g_inv =
      [   4.526935   0.996016   0.276091   0.082237   0.021801   0.003931 ]}}


val basis : Basis.t =
  
                          Atomic Basis set
                          ----------------

-----------------------------------------------------------------------
 #   Angular   Coordinates (Bohr)       Exponents       Coefficients
    Momentum  X        Y        Z
-----------------------------------------------------------------------
  1-3  S   0.0000   0.0000   0.0000   3.04752488e+03    1.83473713e-03
                                      4.57369518e+02    1.40373228e-02
                                      1.03948685e+02    6.88426223e-02
                                      2.92101553e+01    2.32184443e-01
                                      9.28666296e+00    4.67941348e-01
                                      3.16392696e+00    3.62311985e-01
                                    
                                      7.86827235e+00   -1.19332420e-01
                                      1.88128854e+00   -1.60854152e-01
                                    

val aux_basis : Basis.t =
  
                          Atomic Basis set
                          ----------------

-----------------------------------------------------------------------
 #   Angular   Coordinates (Bohr)       Exponents       Coefficients
    Momentum  X        Y        Z
-----------------------------------------------------------------------
  1-6  S   0.0000   0.0000   0.0000   3.04752488e+03    1.83473713e-03
                                      4.57369518e+02    1.40373228e-02
                                      1.03948685e+02    6.88426223e-02
                                      2.92101553e+01    2.32184443e-01
                                      9.28666296e+00    4.67941348e-01
                                      3.16392696e+00    3.62311985e-01
                                    
                                      7.86827235e+00   -1.19332420e-01
                                      1.88128854e+00   -1.60854152e-01
                                

val charge : int = 0


val simulation : Simulation.t = <abstr>


In [11]:
let n_elec_alfa, n_elec_beta, n_elec = 
  let e =  Simulation.electrons simulation in
  Electrons.(n_alfa e, n_beta e, n_elec e)

val n_elec_alfa : int = 3
val n_elec_beta : int = 3
val n_elec : int = 6


### Hartree-Fock

In [12]:
let hf =  HartreeFock.make ~guess:`Hcore ~max_scf:1 simulation  ;;

let mo_basis = MOBasis.of_hartree_fock hf

15 significant shell pairs computed in 0.030632 seconds
1
2
3
6
Computed ERIs in 0.141639 seconds
MOs =


            -- 1 --     -- 2 --    -- 3 --      -- 4 --   -- 5 --
            1      0.995189   -0.236456         -0           -0         0
            2     0.0272807    0.573253         -0           -0         0
            3   -0.00753288     0.50151         -0 -6.64951E-16         0
                        ...         ...        ...          ...       ...
            7            -0          -0 -0.0346136    -0.103467  0.874392
            8            -0 6.53154E-16   0.374215   -0.0232294 0.0788015
            9            -0  7.4731E-16 0.00656013     0.779165  0.118461
      

             -- 6 --   -- 7 --   -- 8 --   -- 9 --
            1              0 0.0649867        -0        -0
            2   -1.35345E-15  -1.62901        -0        -0
            3    7.04525E-16   1.63955        -0        -0
                         ...       ...       ...       ...
            7  

val hf : HartreeFock.t = 
                        Restricted Hartree-Fock                      

    ------------------------------------------------------------
        #     HF energy       Convergence  HOMO-LUMO
    ------------------------------------------------------------
        1    -36.54848150      7.4861e-01     0.2723
    ------------------------------------------------------------


               One-electron energy  -52.6699343629
                           Kinetic   42.4526846308
                         Potential  -95.1226189937
      --------------------------------------------------------  
               Two-electron energy   16.1214528647
                           Coulomb   21.8535626014
                          Exchange   -5.7321097367
      --------------------------------------------------------  
                           HF HOMO    0.8237527941
                           HF LUMO    8.2337246898
                      HF LUMO-LUMO    7.4099718957
      -----

val mo_basis : MOBasis.t =
  Eigenvalues:   -11.127416    -0.632049    -0.269831     0.131526     0.151773 
              -- 1 --     -- 2 --    -- 3 --      -- 4 --   -- 5 --
      1      0.995189   -0.236456         -0           -0         0
      2     0.0272807    0.573253         -0           -0         0
      3   -0.00753288     0.50151         -0 -6.64951E-16         0
                  ...         ...        ...          ...       ...
      7            -0          -0 -0.0346136    -0.103467  0.874392
      8            -0 6.53154E-16   0.374215   -0.0232294 0.0788015
      9            -0  7.4731E-16 0.00656013     0.779165  0.118461
  
  Eigenvalues:     0.786913     0.828232     0.869410     0.849164 
               -- 6 --   -- 7 --   -- 8 --   -- 9 --
      1              0 0.0649867        -0        -0
      2   -1.35345E-15  -1.62901        -0        -0
      3    7.04525E-16   1.63955        -0        -0
                   ...       ...       ...       ...
      7     

# FCI-F12

## Common functions

In [13]:
let f12 = Util.of_some @@ Simulation.f12 simulation 

let mo_num = MOBasis.size mo_basis 

let pp_spindet = Spindeterminant.pp mo_num

let pp_det = Determinant.pp mo_num

;;

#install_printer pp_spindet ;;
#install_printer pp_det ;;



val f12 : F12factor.t =
  {F12factor.expo_s = 1.;
   gaussian =
    {GaussianOperator.coef_g =
      [  -0.314400  -0.303700  -0.168100  -0.098110  -0.060240  -0.037260 ];
     expo_g =
      [   0.220900   1.004000   3.622000  12.160000  45.870000 254.400000 ];
     expo_g_inv =
      [   4.526935   0.996016   0.276091   0.082237   0.021801   0.003931 ]}}


val mo_num : int = 9


val pp_spindet : Format.formatter -> Spindeterminant.t -> unit = <fun>


val pp_det : Format.formatter -> Determinant.t -> unit = <fun>


In [17]:
let simulation_aux = 
    let charge        = Charge.to_int @@ Simulation.charge simulation 
    and multiplicity  = Electrons.multiplicity @@ Simulation.electrons simulation
    and nuclei        = Simulation.nuclei simulation
    in
    let general_basis = 
      Basis.general_basis @@ Simulation.basis simulation
    in
    GeneralBasis.combine [
      general_basis ; GeneralBasis.read aux_basis_filename
    ]
    |> Basis.of_nuclei_and_general_basis ~f12 nuclei
    |> Simulation.make ~charge ~multiplicity ~nuclei 


let aux_basis = 
  MOBasis.of_mo_basis simulation_aux mo_basis

let aux_num = 
  MOBasis.size aux_basis


val simulation_aux : Simulation.t = <abstr>


66 significant shell pairs computed in 0.170052 seconds
1
2
3
6
9
10
11
12
15
18
Computed ERIs in 3.375684 seconds


val aux_basis : MOBasis.t =
  Eigenvalues:   -11.127416    -0.632049    -0.269831     0.131526     0.151773 
               -- 1 --   -- 2 --      -- 3 --     -- 4 --      -- 5 --
       1      0.995189 -0.236456 -6.99905E-13 3.74871E-12 -1.80137E-11
       2     0.0272807  0.573253   1.6881E-12 1.54414E-12  2.46497E-12
       3   -0.00753288   0.50151  2.32851E-13 4.16589E-13  1.21024E-12
                   ...       ...          ...         ...          ...
      22             0         0           -0           0            0
      23             0         0           -0           0            0
      24             0         0           -0           0            0
  
  Eigenvalues:     0.786913     0.828232     0.869410     0.849164     1.480837 
               -- 6 --   -- 7 --      -- 8 --      -- 9 --  -- 10 --
       1   2.65719E-12 0.0649867  3.37785E-12  1.73781E-11         0
       2   2.11976E-13  -1.62901  3.37812E-13   3.5811E-12         0
       3    -1.352E-13   1.63955

val aux_num : int = 23


In [18]:
let () = ignore @@ MOBasis.f12_ints   aux_basis
let () = ignore @@ MOBasis.two_e_ints aux_basis

66 significant shell pairs computed in 2.944168 seconds
1
2
3
6
9
10
11
12
15
18
Computed ERIs in 47.577040 seconds


4-idx transformation 
23 / 23
4-idx transformation 
23 / 23


## Integral-based functions

\begin{equation}
\langle I | \hat{H} | J \rangle = \begin{cases}
\sum_i h_{ii} + \frac{1}{2} \sum_{ij} \langle ij || ij \rangle \text{ when } |J\rangle = |I\rangle \\
h_{ik} + \sum_{j} \langle ij || kj \rangle \text{ when } |J\rangle = \hat{T}_i^k |I\rangle \\
\langle ij || kl \rangle \text{ when } |J\rangle = \hat{T}_{ij}^{kl} |I\rangle \\
\end{cases}
\end{equation}


\begin{equation}
\langle I | \hat{F} | J \rangle = \begin{cases}
\sum_i f_{ii} + \frac{1}{2} \sum_{ij} \langle ij || ij \rangle \text{ when } |J\rangle = |I\rangle \\
f_{ik} + \sum_{j} \langle ij || kj \rangle \text{ when } |J\rangle = \hat{T}_i^k |I\rangle \\
\langle ij || kl \rangle \text{ when } |J\rangle = \hat{T}_{ij}^{kl} |I\rangle \\
\end{cases}
\end{equation}

In [19]:
let cancel_singles = false 

let mos_cabs = 
  Util.list_range (mo_num+1) aux_num
  
let mos_abs = 
  Util.list_range 1 aux_num
  
let mos_in = 
  Util.list_range 1 mo_num

let mos_a k =
  Determinant.alfa k
  |> Spindeterminant.to_list
  
let mos_b k =
  Determinant.beta k
  |> Spindeterminant.to_list
  

val cancel_singles : bool = false


val mos_cabs : int list =
  [10; 11; 12; 13; 14; 15; 16; 17; 18; 19; 20; 21; 22; 23]


val mos_abs : int list =
  [1; 2; 3; 4; 5; 6; 7; 8; 9; 10; 11; 12; 13; 14; 15; 16; 17; 18; 19; 20; 21;
   22; 23]


val mos_in : int list = [1; 2; 3; 4; 5; 6; 7; 8; 9]


val mos_a : Determinant.t -> int list = <fun>


val mos_b : Determinant.t -> int list = <fun>


### H integrals

In [20]:
let h_one =
  let h = 
    MOBasis.one_e_ints aux_basis
  in fun i j _ -> h.{i,j}
  
let h_two = 
  let two_e_ints = MOBasis.two_e_ints aux_basis in
  let h2 i j k l (s:Spin.t) (s':Spin.t) =
    if s' <> s then
        ERI.get_phys two_e_ints i j k l
    else
        (ERI.get_phys two_e_ints i j k l) -.                                                 
        (ERI.get_phys two_e_ints i j l k)
  in
  h2

    
  

val h_one : int -> int -> '_weak1 -> float = <fun>


val h_two : int -> int -> int -> int -> Spin.t -> Spin.t -> float = <fun>


### F12 integrals

In [21]:
let f_two = 
  let two_e_ints = MOBasis.f12_ints aux_basis in
  let f2 i j k l (s:Spin.t) (s':Spin.t) =
    if s' <> s then
        0.5 *. F12.get_phys two_e_ints i j k l
    else
        0.5 *. (
         (F12.get_phys two_e_ints i j k l) -.                                                 
         (F12.get_phys two_e_ints i j l k) )
  in
  let f3 i j k l (s:Spin.t) (s':Spin.t) = 
      if (i=k && j<>l) || (j=l && i<>k) then
        0.
      else
        f2 i j k l s s'
  in
  if cancel_singles then f3 else f2

let f_one = fun _ _ _ -> 0.

(*
let f_two = h_two

let f_one = h_one
*)


val f_two : int -> int -> int -> int -> Spin.t -> Spin.t -> float = <fun>


val f_one : 'a -> 'b -> 'c -> float = <fun>


## Determinant-based functions

### Integrals

In [22]:
let f12_integrals mo_basis =
  ( f_one, f_two, None )

let h_ij mo_basis ki kj =
  let integrals =
    List.map (fun f -> f mo_basis)
      [ CI.h_integrals ]
  in
  CIMatrixElement.make integrals ki kj 
  |> List.hd


let f_ij mo_basis ki kj =
  let integrals =
    List.map (fun f -> f mo_basis)
      [ f12_integrals ]
  in
  CIMatrixElement.make integrals ki kj 
  |> List.hd                                                                                  


let hf_ij mo_basis ki kj =
  let integrals =
    List.map (fun f -> f mo_basis)
      [ CI.h_integrals ; f12_integrals ]
  in
  CIMatrixElement.make integrals ki kj




val f12_integrals :
  'a ->
  ('b -> 'c -> 'd -> float) *
  (int -> int -> int -> int -> Spin.t -> Spin.t -> float) * 'e option = <fun>


val h_ij : MOBasis.t -> CIMatrixElement.De.t -> CIMatrixElement.De.t -> float =
  <fun>


val f_ij : 'a -> CIMatrixElement.De.t -> CIMatrixElement.De.t -> float =
  <fun>


val hf_ij :
  MOBasis.t -> CIMatrixElement.De.t -> CIMatrixElement.De.t -> float list =
  <fun>


### Determinant space

In [23]:
let is_a_double det_space =
    let mo_class = DeterminantSpace.mo_class det_space in
    let mo_num = Array.length @@ MOClass.mo_class_array mo_class in
    let m l =
      List.fold_left (fun accu i ->
          let j = i-1 in Bitstring.logor accu (Bitstring.shift_left_one mo_num j)
        ) (Bitstring.zero mo_num) l
    in
    let aux_mask   = m (MOClass.auxiliary_mos mo_class) in
    fun k ->                                                                                  
      let alfa =
        Determinant.alfa k
        |> Spindeterminant.bitstring
      in
      let beta =
        Determinant.beta k
        |> Spindeterminant.bitstring
      in
      let a = Bitstring.logand aux_mask alfa
      and b = Bitstring.logand aux_mask beta
      in
      match Bitstring.popcount a + Bitstring.popcount b with
      | 2 | 1 -> true
      | 0 | _ -> false



val is_a_double : DeterminantSpace.t -> Determinant.t -> bool = <fun>


In [24]:
let in_space = 
    DeterminantSpace.fci_f12_of_mo_basis aux_basis ~frozen_core mo_num
    
let aux_space = 
    DeterminantSpace.fci_of_mo_basis aux_basis ~frozen_core 

let det_space_in () =
    DeterminantSpace.determinant_stream in_space

let det_space_out () =
    let s = 
        DeterminantSpace.determinant_stream aux_space
    in
    Stream.from (fun _ ->
        try
          let is_a_double = is_a_double in_space in
          let rec result () =
            let ki = Stream.next s in
            if is_a_double ki then
              Some (ki,ki)
            else
              result ()
          in
          result ()
        with Stream.Failure -> None
      )
    

Number of determinants : 84 84 7056


val in_space : DeterminantSpace.t = <abstr>


Number of determinants : 1771 1771 3136441


val aux_space : DeterminantSpace.t = <abstr>


val det_space_in : unit -> Determinant.t Stream.t = <fun>


val det_space_out : unit -> (Determinant.t * Determinant.t) Stream.t = <fun>


In [25]:
let ci = CI.make ~n_states:state in_space

let ci_coef, ci_energy = Lazy.force ci.eigensystem 

let _ = print_newline () 


val ci : CI.t =
  {CI.e_shift = -37.5503734698766749; det_space = <abstr>; m_H = <lazy>;
   m_S2 = <lazy>; eigensystem = <lazy>; n_states = 1}


  1     0.0000000000    4.27876562e-01
  2    -0.0892428622    1.30475694e-01
  3    -0.0992140908    8.74622552e-02
  4    -0.1022422166    2.82063810e-02
  5    -0.1043598897    3.75067379e-02
  6    -0.1065557159    4.71900677e-02
  7    -0.1080257508    1.17050850e-02
  8    -0.1082438353    4.19578665e-03
  0    -0.1082636845    1.74312819e-03
  1    -0.1082673418    7.12907013e-04
  2    -0.1082677387    3.29773623e-04
  3    -0.1082678068    1.62017164e-04
  4    -0.1082678363    1.97376384e-04
  5    -0.1082678767    1.65667212e-04
  6    -0.1082678966    1.24231166e-04
  7    -0.1082679014    1.06697750e-05
  8    -0.1082679016    5.05286931e-06
  0    -0.1082679016    2.52890819e-06


val ci_coef : Lacaml.D.Mat.t =
  

                -- 1 --
           1      -0.780949
           2             -0
           3             -0
                        ...
        7054             -0
        7055             -0
        7056   -3.12865E-06
  
val ci_energy : Lacaml.D.Vec.t =
        R1       R2       R3
  -37.6586 -36.7238 -36.2286


  1    -0.1082679016    4.37907116e-07



- : unit = ()


Permutation operator $p_{12}$ that generates a new determinant with electrons 1 and 2 swapped.

## Matrices $\langle I | H | \alpha \rangle$ and $\langle I | F | \alpha \rangle$ 

In [26]:
let randomize = false

let out_list =
    Util.stream_to_list (det_space_out ())
    
let in_list =
    Util.stream_to_list (det_space_in ())
    
let det_a = Array.of_list out_list
            |> Array.map (fun (i,_) -> i)

let det_I =
  if randomize then
    let n = 123456789 in
    in_list
    |> List.map (fun k -> (Random.int n, k))
    |> List.sort compare
    |> List.map  (fun (_,k) -> k)
    |> Array.of_list
  else
    Array.of_list in_list


val randomize : bool = false


val out_list : (Determinant.t * Determinant.t) list =
  [(phase:+1
    a:+1 ++-------+------------------------------------------------------
    b:+1 +++-------------------------------------------------------------
,
phase:+1
a:+1 ++-------+------------------------------------------------------
b:+1 +++-------------------------------------------------------------
);
(phase:+1
 a:+1 +-+------+------------------------------------------------------
 b:+1 +++-------------------------------------------------------------
,
phase:+1
a:+1 +-+------+------------------------------------------------------
b:+1 +++-------------------------------------------------------------
);
(phase:+1
 a:+1 -++------+------------------------------------------------------
 b:+1 +++-------------------------------------------------------------
,
phase:+1
a:+1 -++------+------------------------------------------------------
b:+1 +++-------------------------------------------------------------
);
(phase:+1
 a:+1 +--

val in_list : Determinant.t list =
  [phase:+1
   a:+1 +++-------------------------------------------------------------
   b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 ++-+------------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 +-++------------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 -+++------------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 ++--+-----------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 +-+-+-----------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 -++-+-------------------------------

val det_a : Determinant.t array =
  [|phase:+1
    a:+1 ++-------+------------------------------------------------------
    b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 +-+------+------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 -++------+------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 +--+-----+------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 -+-+-----+------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 --++-----+------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 +---+----+------------------------

val det_I : Determinant.t array =
  [|phase:+1
    a:+1 +++-------------------------------------------------------------
    b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 ++-+------------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 +-++------------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 -+++------------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 ++--+-----------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 +-+-+-----------------------------------------------------------
b:+1 +++-------------------------------------------------------------
;
phase:+1
a:+1 -++-+-----------------------------

Function to generate all intermediate external determinants $|\alpha \rangle$ between $|I\rangle$ and $|J\rangle$, with a positive phase factor.

* `exc` is the degree of excitation between $|I\rangle$ and $|J\rangle$

In [27]:
let generate_alphas ki kj exc =
  (* Check input excitation degree *)
  let d = Determinant.degree ki kj in
  if d <> exc then
    Printf.sprintf "Invalid excitation degree. Expected %d and found %d." exc d
    |> failwith;
    
  (* Generate single excitations *)
  let all_singles ki =
      let mos_a, mos_b = Determinant.to_lists ki in
      [ List.map (fun hole -> 
          List.map (fun particle ->
               if hole = particle then None else
                  Some (Determinant.single_excitation Spin.Alfa hole particle ki)
              ) mos_abs
          ) mos_a
      ;
        List.map (fun hole -> 
          List.map (fun particle ->
               if hole = particle then None else
                 Some (Determinant.single_excitation Spin.Beta hole particle ki)
              ) mos_abs
          ) mos_b 
      ]
      |> List.concat
      |> List.concat
      |> Util.list_some
      |> List.filter (fun x -> Determinant.is_none x = false)
      |> List.map (fun x -> Determinant.set_phase Phase.Pos x)
  in
  
  (* Generate double excitations *)
  let all_doubles ki =
      let mos_a, mos_b = Determinant.to_lists ki in
      [ List.map (fun hole ->  (* Alpha-Alpha *)
          List.map (fun particle ->
            List.map (fun hole' -> 
              List.map (fun particle' ->
                if hole = particle || hole' = particle' then None else
                if hole' > hole && particle' < particle then
                  Some (Determinant.double_excitation Spin.Alfa hole particle Spin.Alfa hole' particle' ki)
                else None
                      ) mos_abs
                  ) mos_a 
              ) mos_abs
          ) mos_a
        ; 
        List.map (fun hole ->  (* Beta-Beta *)
          List.map (fun particle ->
            List.map (fun hole' -> 
              List.map (fun particle' ->
                if hole' > hole && particle' < particle && hole <> particle && hole' <> particle' then
                  Some (Determinant.double_excitation Spin.Beta hole particle Spin.Beta hole' particle' ki)
                else None
                      ) mos_abs
                  ) mos_b 
              ) mos_abs
          ) mos_b
        ;
        List.map (fun hole ->  (* Alpha-Beta *)
          List.map (fun particle ->
            List.map (fun hole' -> 
              List.map (fun particle' ->
                  if hole = particle || hole' = particle' then None else
                  Some (Determinant.double_excitation Spin.Alfa hole particle Spin.Beta hole' particle' ki)
                      ) mos_abs
                  ) mos_b 
              ) mos_abs
          ) mos_a
      ]
      |> List.concat
      |> List.concat
      |> List.concat
      |> List.concat
      |> Util.list_some
      |> List.filter (fun x -> Determinant.is_none x = false)
      |> List.map (fun x -> Determinant.set_phase Phase.Pos x)
  in

  (* Generate left and right excitations *)
  let al = List.concat [ all_singles ki ; all_doubles ki ] in
  let ar = List.concat [ all_singles kj ; all_doubles kj ] in
  
  let mo_class = DeterminantSpace.mo_class in_space in
  let m l =
    List.fold_left (fun accu i ->
        let j = i-1 in Bitstring.logor accu (Bitstring.shift_left_one mo_num j)
      ) (Bitstring.zero mo_num) l
  in
  let aux_mask = m (MOClass.auxiliary_mos mo_class) in
  let good_cabs k = 
      let alfa =
        Determinant.alfa k
        |> Spindeterminant.bitstring
      in
      let beta =
        Determinant.beta k
        |> Spindeterminant.bitstring
      in
      let a = Bitstring.logand aux_mask alfa
      and b = Bitstring.logand aux_mask beta
      in
      match Bitstring.popcount a + Bitstring.popcount b with
      | 1 | 2 -> true
      | _ -> false
  in
  
  (* Merge lists in a set of unique determinants *)
  List.concat [ al; ar ]
  |> List.sort_uniq compare
  
  (* Filter out all determinants with incorrect numbers of electrons in the CABS *)
  |> List.filter good_cabs 
  
  
let compute_HaaF ki alphas kj =
   List.fold_left (fun accu alpha -> accu
      +. h_ij aux_basis ki alpha
      *. f_ij aux_basis alpha kj
    ) 0. alphas


val generate_alphas :
  Determinant.t -> Determinant.t -> int -> Determinant.t list = <fun>


val compute_HaaF :
  CIMatrixElement.De.t ->
  CIMatrixElement.De.t list -> CIMatrixElement.De.t -> float = <fun>


In [28]:
let check n integral_value exc =
  let cpudet, cpuint = ref 0., ref 0. in
  let det_list =
      match n with
        | 0 -> det_I
        | n -> Array.sub det_I 0 n
  in
  let result =
        Printf.printf "Checking ... \n%!";
        let percent = ref 0 in
        let task (i,ki) =
            (let p = (10 * (i+1))/(Array.length det_list) in
            if p <> !percent then
                ( percent := p ; Printf.printf " - %3d %%\n%!" (p*10) ));
            Array.mapi (fun j kj -> 
                if i > j || Determinant.degree ki kj <> exc then
                    (0,0,0.,0.)
                else
                  begin
                    let alphas = generate_alphas ki kj exc in
                    let det_value =
                      let t0 = Unix.gettimeofday () in
                      let result = compute_HaaF ki alphas kj in
                      cpudet := !cpudet +. Unix.gettimeofday () -. t0;
                      result
                    in
                    let int_value = 
                      let t0 = Unix.gettimeofday () in
                      let result = integral_value ki kj in
                      cpuint := !cpuint +. Unix.gettimeofday () -. t0;
                      result
                    in
(*   Printf.printf "%d %d %e %e\n%!" i j det_value int_value;  *)
                    (i,j,det_value,int_value)
                  end
            ) det_list
        in
        det_list
        |> Array.mapi (fun i ki -> (i,ki))
        |> Array.to_list
        |> Stream.of_list
        |> Farm.run ~f:task
        |> Util.stream_to_list
        |> Array.concat
  in
  let i,j,d,v = 
      let rec aux k imax jmax emax dmax vmax = 
        if k = -1 then
          imax, jmax, dmax, vmax
        else
          let i, j, d, v = result.(k) in
          let e = abs_float (d -. v) in
          if e >= emax then
            aux (k-1) i j e d v
          else
            aux (k-1) imax jmax emax dmax vmax
      in
      aux (Array.length result - 1) 0 0 0. 0. 0.
  in
  let error = abs_float (d -. v) in
  if error < epsilon_float then
  (*
      Printf.printf "OK: %e\n%!" error
      *)
      Printf.printf "OK: (%d, %d) | %e %e | %e  |  cpu : %f  %f\n%!" i j d v error !cpudet !cpuint
  else
      Printf.printf "Failed: (%d, %d) | %e %e | %e  |  cpu : %f %f\n%!" i j d v error !cpudet !cpuint

    
let sum l f = List.fold_left (fun accu i -> accu +. f i) 0. l

val check :
  int ->
  (CIMatrixElement.De.t -> CIMatrixElement.De.t -> float) -> int -> unit =
  <fun>


val sum : 'a list -> ('a -> float) -> float = <fun>


In [29]:
let array_3_init d1 d2 d3 f =
  let result = 
      Bigarray.(Array3.create Float64 fortran_layout) d1 d2 d3
  in
  for k=1 to d3 do
      for j=1 to d2 do
          for i=1 to d1 do
             result.{i,j,k} <- f i j k
          done
      done
  done;
  result


let array_4_init d1 d2 d3 d4 f =
  let result = 
      Bigarray.(Genarray.create Float64 fortran_layout) [| d1;d2;d3;d4 |]
  in
  for l=1 to d4 do
    for k=1 to d3 do
      for j=1 to d2 do
        for i=1 to d1 do
           result.{i,j,k,l} <- f i j k l
        done
      done
    done
  done;
  result


let array_5_init d1 d2 d3 d4 d5 f =
  let result = 
      Bigarray.(Genarray.create Float64 fortran_layout) [| d1;d2;d3;d4;d5 |]
  in
  for m=1 to d5 do
    for l=1 to d4 do
      for k=1 to d3 do
        for j=1 to d2 do
          for i=1 to d1 do
             result.{i,j,k,l,m} <- f i j k l m
          done
        done
      done
    done
  done;
  result

(* ----- *)

val array_3_init :
  int ->
  int ->
  int ->
  (int -> int -> int -> float) ->
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Array3.t =
  <fun>


val array_4_init :
  int ->
  int ->
  int ->
  int ->
  (int -> int -> int -> int -> float) ->
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <fun>


val array_5_init :
  int ->
  int ->
  int ->
  int ->
  int ->
  (int -> int -> int -> int -> int -> float) ->
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <fun>


******

# 1. 0 

In [30]:
let m_0111_1H_1F = 
  Vec.init mo_num (fun i -> 
        sum mos_cabs (fun a ->
            h_one i a Spin.Alfa *. f_one a i Spin.Alfa ))

let m_0111_1H_2Fa, m_0111_2Ha_2Fa =

    let m_0122_Haa = 
      array_3_init mo_num mo_num mo_num (fun i j k ->
          sum mos_cabs (fun a ->
            h_two i j a k Spin.Alfa Spin.Alfa *. f_two a k i j Spin.Alfa Spin.Alfa
            ) )
    in      
    
    let m_0111_1H_2Fa = 
      Mat.init_cols mo_num mo_num (fun i j ->
          sum mos_cabs (fun a ->
            h_one i a Spin.Alfa *. f_two a j i j Spin.Alfa Spin.Alfa +.
            h_two i j a j Spin.Alfa Spin.Alfa *. f_one a i Spin.Alfa
          ) +.
          if i < j then 0. else
              begin
                  sum mos_cabs (fun a ->
                      sum mos_cabs (fun b -> if b >= a then 0. else
                        h_two i j a b Spin.Alfa Spin.Alfa *. f_two a b i j Spin.Alfa Spin.Alfa
                      )
                  ) +.
                  sum mos_in (fun k -> m_0122_Haa.{i,j,k}) 
              end
      )
    in
    
    let m_0111_2Ha_2Fa =
      array_3_init mo_num mo_num mo_num (fun i j k ->
        sum mos_cabs (fun a ->
          h_two i j a j Spin.Alfa Spin.Alfa *.
          f_two a k i k Spin.Alfa Spin.Alfa 
        ) -. if i < j then 0. else m_0122_Haa.{i,j,k}
      )
    in m_0111_1H_2Fa, m_0111_2Ha_2Fa


    
let m_0111_1H_2Fb, m_0111_2Hb_2Fb =
    let m_0122_Hab = 
      array_3_init mo_num mo_num mo_num (fun i j k ->
          sum mos_cabs (fun a ->
             h_two i j a k Spin.Alfa Spin.Beta *. f_two a k i j Spin.Alfa Spin.Beta
          ) )
    in
    
    let m_0111_1H_2Fb = 
      Mat.init_cols mo_num mo_num (fun i j ->
          sum mos_cabs (fun a ->
            h_one i a Spin.Alfa *. f_two a j i j Spin.Alfa Spin.Beta +. 
            h_two i j a j Spin.Alfa Spin.Beta *. f_one a i Spin.Alfa +.
            h_one j a Spin.Alfa *. f_two a i j i Spin.Alfa Spin.Beta +. 
            h_two j i a i Spin.Alfa Spin.Beta *. f_one a j Spin.Alfa
          ) +.
        sum mos_in (fun k -> m_0122_Hab.{i,j,k} +. m_0122_Hab.{j,i,k} ) +.
        sum mos_cabs (fun a ->
            sum mos_cabs (fun b ->
            h_two i j a b Spin.Alfa Spin.Beta *. f_two a b i j Spin.Alfa Spin.Beta
            )
          )
        )
    in    
    
    let m_0111_2Hb_2Fb =
      array_3_init mo_num mo_num mo_num (fun i j k ->
        sum mos_cabs (fun a ->
          h_two k i a i Spin.Alfa Spin.Beta *.
          f_two a j k j Spin.Alfa Spin.Beta +.
          h_two i k a k Spin.Alfa Spin.Beta *.
          f_two a j i j Spin.Alfa Spin.Alfa 
        ) -. m_0122_Hab.{k,i,j}
      )
    in
    m_0111_1H_2Fb, m_0111_2Hb_2Fb
    

let m_0111_2Ha_2Fb =
  array_3_init mo_num mo_num mo_num (fun i j k ->
    sum mos_cabs (fun a ->
      h_two i j a j Spin.Alfa Spin.Alfa *.
      f_two a k i k Spin.Alfa Spin.Beta 
    )
  )




let integral_value ki kj = 

   let mos_i, mos_i' = mos_a ki, mos_b ki in
   let same = (mos_i = mos_i') in
   
   (* Alpha *)
   let a = 
       sum mos_i  (fun i -> m_0111_1H_1F.{i}) 
   in
   
   let b = 
       if same then a else
       sum mos_i' (fun i -> m_0111_1H_1F.{i})
   in
   
   let aa = 
       sum mos_i (fun j ->
         sum mos_i (fun i -> m_0111_1H_2Fa.{i,j} ))
   in
   
   let bb = 
     if same then aa else
     sum mos_i' (fun j ->
       sum mos_i' (fun i -> m_0111_1H_2Fa.{i,j} ))
   in
   
   let ab = 
     sum mos_i' (fun j ->
       sum mos_i (fun i -> m_0111_1H_2Fb.{i,j}  )) 
   in
   
   let aaa = 
       sum mos_i (fun k ->
         sum mos_i (fun j ->
           sum mos_i (fun i -> m_0111_2Ha_2Fa.{i,j,k} ))) 
   in
   
   let bbb = 
     if same then aaa else
       sum mos_i' (fun k ->
         sum mos_i' (fun j ->
           sum mos_i' (fun i -> m_0111_2Ha_2Fa.{i,j,k} )))
   in
   
   let baa = 
       sum mos_i' (fun k ->
         sum mos_i (fun j ->
           sum mos_i (fun i ->
             m_0111_2Ha_2Fb.{i,j,k} +. m_0111_2Hb_2Fb.{i,j,k}
       )))
   in
   
   let bba = 
       sum mos_i  (fun k ->
         sum mos_i' (fun j ->
           sum mos_i' (fun i ->
             m_0111_2Ha_2Fb.{i,j,k} +. m_0111_2Hb_2Fb.{j,i,k} 
       ))) 
   in

   a +. b +. aa +. bb +. ab +. aaa +. baa +. bba +. bbb
   
     
let _ =
  check 0 integral_value 0 
    
    

val m_0111_1H_1F : Lacaml.D.vec = R1 R2 R3     R7 R8 R9
                                   0  0  0 ...  0  0  0


val m_0111_1H_2Fa : Lacaml.D.mat =
  

            -- 1 --     -- 2 --     -- 3 --     -- 4 --     -- 5 --
        1             0 4.14783E-05 0.000191898   5.819E-05 3.17034E-05
        2    0.00285395           0  0.00130169 0.000700753 0.000516776
        3     0.0048103 0.000752348           0  0.00113768 0.000719116
                    ...         ...         ...         ...         ...
        7   -0.00384068 -0.00136624 -0.00343863 -0.00255958 -0.00227812
        8     0.0164152   0.0118156   0.0104307  0.00609247  0.00526221
        9     0.0169861   0.0119274    0.010345  0.00631195  0.00505777
  

            -- 6 --      -- 7 --     -- 8 --     -- 9 --
        1   0.000201004 -1.30762E-06 0.000334712 0.000361198
        2   0.000232139  -0.00168234  0.00083308  0.00101706
        3   -0.00387497  0.000450355  0.00302132  0.00343988
                    ...          ...         ...         ...
        7   -0.00166296            0  0.00138345  0.00154153
        8    0.00316903

val m_0111_1H_2Fb : Lacaml.D.mat =
  

            -- 1 --     -- 2 --     -- 3 --     -- 4 --      -- 5 --
        1    0.00296502  0.00298831  0.00488797 0.000118822 -0.000472343
        2    0.00298831 -0.00136007 -0.00413131  -0.0063196  -0.00598212
        3    0.00488797 -0.00413131 -0.00712707 -0.00508589  -0.00503032
                    ...         ...         ...         ...          ...
        7   -0.00407169 -0.00213075  -0.0040668 -0.00417519  -0.00370227
        8     0.0160284   0.0113906   0.0122954  0.00422564   0.00433285
        9     0.0166196   0.0110531   0.0122398  0.00511694    0.0023468
  

           -- 6 --     -- 7 --   -- 8 --    -- 9 --
        1    0.0112593 -0.00407169 0.0160284  0.0166196
        2   0.00920231 -0.00213075 0.0113906  0.0110531
        3   0.00825183  -0.0040668 0.0122954  0.0122398
                   ...         ...       ...        ...
        7    0.0043954 -0.00205631 0.0045038 0.00403087
        8    0.0150589   0.0045038 0.0198249 

val m_0111_2Ha_2Fb :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Array3.t =
  <abstr>


val integral_value : Determinant.t -> 'a -> float = <fun>


Checking ... 
 -  10 %
 -  20 %
 -  30 %
 -  40 %
 -  50 %
 -  60 %
 -  70 %
 -  80 %
 -  90 %
 - 100 %
Failed: (5594, 5594) | -2.621269e-01 -2.621269e-01 | 9.992007e-16  |  cpu : 605.920079 0.214178


- : unit = ()


# 2. 1

In [31]:
let m_1111_1H_1F = 
  Mat.init_cols mo_num mo_num (fun i k -> 
        sum mos_cabs (fun a -> h_one i a Spin.Alfa *. f_one a k Spin.Alfa ))


    

let m_1111_2Ha_2Fa =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    if l=i then
        sum mos_cabs (fun a ->
          h_two j l a l Spin.Alfa Spin.Alfa *.
          f_two a i j k Spin.Alfa Spin.Alfa 
        )
    else
        sum mos_cabs (fun a ->
          h_two i j a j Spin.Alfa Spin.Alfa *.
          f_two a l k l Spin.Alfa Spin.Alfa +.
          h_two j l a l Spin.Alfa Spin.Alfa *.
          f_two a i j k Spin.Alfa Spin.Alfa )
  )



let m_1111_2Hb_2Fa =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    if l=i then
        sum mos_cabs (fun a ->
          h_two j l a l Spin.Alfa Spin.Beta *.
          f_two a i j k Spin.Alfa Spin.Beta 
        )
    else
        sum mos_cabs (fun a ->
          h_two i j a j Spin.Alfa Spin.Beta *.
          f_two a l k l Spin.Alfa Spin.Alfa +.
          h_two j l a l Spin.Alfa Spin.Beta *.
          f_two a i j k Spin.Alfa Spin.Beta 
        )
  )


let m_1111_2Ha_2Fb =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    sum mos_cabs (fun a ->
      h_two i j a j Spin.Alfa Spin.Alfa *.
      f_two a l k l Spin.Alfa Spin.Beta +.
      h_two j l a l Spin.Alfa Spin.Beta *.
      f_two a i j k Spin.Alfa Spin.Alfa 
    )
  )



let m_1111_2Hb_2Fb =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    sum mos_cabs (fun a ->
      h_two i j a j Spin.Alfa Spin.Beta *.
      f_two a l k l Spin.Alfa Spin.Beta +.
      h_two j l a l Spin.Alfa Spin.Alfa *.
      f_two a i j k Spin.Alfa Spin.Beta 
    )
  )




    


let m_1121_2Ha_2Fa =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    sum mos_cabs (fun a ->
      h_two i j k a Spin.Alfa Spin.Alfa *.
      f_two l a l j Spin.Alfa Spin.Alfa 
    )
  )


let m_1121_2Hb_2Fa =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    sum mos_cabs (fun a ->
      h_two i j k a Spin.Alfa Spin.Beta *.
      f_two l a l j Spin.Alfa Spin.Alfa 
    )
  )

let m_1121_2Ha_2Fb =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    sum mos_cabs (fun a ->
      h_two i j k a Spin.Alfa Spin.Alfa *.
      f_two l a l j Spin.Alfa Spin.Beta 
    )
  )


let m_1121_2Hb_2Fb =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    sum mos_cabs (fun a ->
      h_two i j k a Spin.Alfa Spin.Beta *.
      f_two l a l j Spin.Alfa Spin.Beta 
    )
  )

let m_1122_va =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    sum mos_cabs (fun a ->
      h_two j i a l Spin.Alfa Spin.Alfa *.
      f_two l a k j Spin.Alfa Spin.Alfa 
    )
  )
  
let m_1111_1H_2Fa = 
  array_3_init mo_num mo_num mo_num (fun j i k ->
      sum mos_in (fun l -> m_1122_va.{l,j,i,k}) +.
      sum mos_cabs (fun a ->
        h_one i a Spin.Alfa *. f_two a j k j Spin.Alfa Spin.Alfa +.
        h_two i j a j Spin.Alfa Spin.Alfa *. f_one a k Spin.Alfa +.
        h_one j a Spin.Alfa *. f_two a i j k Spin.Alfa Spin.Alfa +.
        h_two i j k a Spin.Alfa Spin.Alfa *. f_one a j Spin.Alfa +.
        sum mos_cabs (fun b -> if b > a then 0. else
          h_two i j a b Spin.Alfa Spin.Alfa *.
          f_two a b k j Spin.Alfa Spin.Alfa )
      )
    )


let m_1122_v2 =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    sum mos_cabs (fun a ->
      h_two i j l a Spin.Alfa Spin.Beta *.
      f_two l a k j Spin.Alfa Spin.Beta 
    )
  )


let m_1122_v3 =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    sum mos_cabs (fun a ->
      h_two i j a l Spin.Alfa Spin.Beta *.
      f_two a l k j Spin.Alfa Spin.Beta 
    )
  )

  
let m_1111_1H_2Fb = 
  array_3_init mo_num mo_num mo_num (fun j i k ->
      sum mos_in (fun l -> m_1122_v2.{l,j,i,k} +. m_1122_v3.{l,j,i,k}) +.
      sum mos_cabs (fun a ->
        h_one i a Spin.Alfa *. f_two a j k j Spin.Alfa Spin.Beta +.
        h_two i j a j Spin.Alfa Spin.Beta *. f_one a k Spin.Alfa +.
        h_one j a Spin.Beta *. f_two a i j k Spin.Alfa Spin.Beta +.
        h_two i j k a Spin.Alfa Spin.Beta *. f_one a j Spin.Beta +.
        sum mos_cabs (fun b ->
          h_two i j a b Spin.Alfa Spin.Beta *.
          f_two a b k j Spin.Alfa Spin.Beta 
        )
      )
    )
  
let m_1122_oa =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
  if l > j then
    sum mos_cabs (fun a ->
      h_two j l a k Spin.Alfa Spin.Alfa *.
      f_two i a l j Spin.Alfa Spin.Alfa 
    )
  else 0.
  )

let m_1122_o =
  array_4_init mo_num mo_num mo_num mo_num (fun l j i k ->
    sum mos_cabs (fun a ->
      h_two l j k a Spin.Alfa Spin.Beta *.
      f_two i a l j Spin.Alfa Spin.Beta 
    )
  )
  


(*----*)

let integral_value ki kj = 
    let i, k, s, phase =
          match Excitation.of_det ki kj with
          | Excitation.(Single (phase, { hole ; particle ; spin })) ->
            hole, particle, spin, phase
          | _ -> assert false
    in
    
    let mos_novirt, mos_novirt' =
      let alfa = 
        let i = Spindeterminant.bitstring @@ Determinant.alfa ki in
        let j = Spindeterminant.bitstring @@ Determinant.alfa kj in
        Bitstring.to_list (Bitstring.logor i j)
      in
      let beta  = 
        let i = Spindeterminant.bitstring @@ Determinant.beta ki in
        let j = Spindeterminant.bitstring @@ Determinant.beta kj in
        Bitstring.to_list (Bitstring.logor i j)
      in
      match s with
      | Spin.Alfa -> alfa, beta
      | Spin.Beta -> beta, alfa
    in
    
    let mos_ij, mos_ij' =
      let alfa = 
        let i = Spindeterminant.bitstring @@ Determinant.alfa ki in
        let j = Spindeterminant.bitstring @@ Determinant.alfa kj in
        Bitstring.to_list (Bitstring.logand i j)
      in
      let beta  = 
        let i = Spindeterminant.bitstring @@ Determinant.beta ki in
        let j = Spindeterminant.bitstring @@ Determinant.beta kj in
        Bitstring.to_list (Bitstring.logand i j)
      in
      match s with
      | Spin.Alfa -> alfa, beta
      | Spin.Beta -> beta, alfa
    in
    
    let mos_i, mos_i' =
      match s with
      | Spin.Alfa -> mos_a ki, mos_b ki
      | Spin.Beta -> mos_b ki, mos_a ki
    in
   
    let mos_j, mos_j' =
      match s with
      | Spin.Alfa -> mos_a kj, mos_b kj
      | Spin.Beta -> mos_b kj, mos_a kj
    in
   
    let result = 
     m_1111_1H_1F.{i,k} +. 
     sum mos_ij (fun j -> 
          m_1111_1H_2Fa.{j,i,k} 
       +. sum mos_i  (fun l -> m_1111_2Ha_2Fa.{l,j,i,k})
       +. sum mos_i' (fun l -> m_1111_2Ha_2Fb.{l,j,i,k})
       +. sum mos_j  (fun l -> m_1121_2Ha_2Fa.{l,j,i,k})
       +. sum mos_j' (fun l -> m_1121_2Ha_2Fb.{l,j,i,k})
       -. sum mos_novirt (fun l -> m_1122_va.{l,j,i,k})
       -. sum mos_ij (fun l -> m_1122_oa.{l,j,i,k} )
       ) +.
     sum mos_ij' (fun j ->
          m_1111_1H_2Fb.{j,i,k} 
       +. sum mos_i  (fun l -> m_1111_2Hb_2Fa.{l,j,i,k})
       +. sum mos_i' (fun l -> m_1111_2Hb_2Fb.{l,j,i,k})
       +. sum mos_j  (fun l -> m_1121_2Hb_2Fb.{l,j,i,k})
       +. sum mos_j' (fun l -> m_1121_2Hb_2Fa.{l,j,i,k})
       -. sum mos_novirt  (fun l ->  m_1122_v2.{l,j,i,k}) 
       -. sum mos_novirt' (fun l ->  m_1122_v3.{l,j,i,k})
       -. sum mos_ij    (fun l ->  m_1122_o.{l,j,i,k})
       ) 
    in
    match phase with
    | Phase.Pos -> result
    | Phase.Neg -> -. result
     

(*
let ki = det_I.(77)
let kj = det_I.(83)

let _ = integral_value ki kj
let _ = 
    let alphas =  generate_alphas ki kj 1 1
    in compute_HaaF ki alphas kj
*)

let _ = check 100 integral_value 1 



val m_1111_1H_1F : Lacaml.D.mat =
  

        -- 1 -- -- 2 -- -- 3 -- -- 4 -- -- 5 --
        1         0       0       0       0       0
        2         0       0       0       0       0
        3         0       0       0       0       0
                ...     ...     ...     ...     ...
        7         0       0       0       0       0
        8         0       0       0       0       0
        9         0       0       0       0       0
  

        -- 6 -- -- 7 -- -- 8 -- -- 9 --
        1         0       0       0       0
        2         0       0       0       0
        3         0       0       0       0
                ...     ...     ...     ...
        7         0       0       0       0
        8         0       0       0       0
        9         0       0       0       0
  


val m_1111_2Ha_2Fa :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <abstr>


val m_1111_2Hb_2Fa :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <abstr>


val m_1111_2Ha_2Fb :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <abstr>


val m_1111_2Hb_2Fb :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <abstr>


...

val m_1122_oa :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <abstr>


val m_1122_o :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <abstr>


val integral_value : Determinant.t -> Determinant.t -> float = <fun>


Checking ... 
 -  10 %
 -  20 %
 -  30 %
 -  40 %
 -  50 %
 -  60 %
 -  70 %
 -  80 %
 -  90 %
 - 100 %
OK: (1, 35) | 1.340491e-02 1.340491e-02 | 2.775558e-17  |  cpu : 79.129396  0.030664


- : unit = ()


# 3. 2

In [129]:
let m_2112_1H_2Fa =
  array_4_init mo_num mo_num mo_num mo_num (fun i j k l ->
    sum mos_cabs (fun a ->
        h_one i a Spin.Alfa *. f_two a j k l Spin.Alfa Spin.Alfa +.
        h_one j a Spin.Alfa *. f_two i a k l Spin.Alfa Spin.Alfa +. 
        h_two i j a l Spin.Alfa Spin.Alfa *. f_one a k Spin.Alfa +.
        h_two i j k a Spin.Alfa Spin.Alfa *. f_one a l Spin.Alfa +.
        sum mos_in  (fun m -> -. h_two i j a m Spin.Alfa Spin.Alfa *.
                                 f_two m a k l Spin.Alfa Spin.Alfa) +.
        sum mos_cabs (fun b -> if b >= a then 0. else
            h_two i j a b Spin.Alfa Spin.Alfa *. f_two a b k l Spin.Alfa Spin.Alfa 
        )
      )
    )

let m_2112_1H_2Fb =
  array_4_init mo_num mo_num mo_num mo_num (fun i j k l ->
    sum mos_cabs (fun a ->
        h_one i a Spin.Alfa *. f_two a j k l Spin.Alfa Spin.Beta +.
        h_one j a Spin.Alfa *. f_two i a k l Spin.Alfa Spin.Beta +.
        h_two i j a l Spin.Alfa Spin.Beta *. f_one a k Spin.Alfa +.
        h_two i j k a Spin.Alfa Spin.Beta *. f_one a l Spin.Alfa +.
        sum mos_in (fun m ->
          h_two i j a m Spin.Alfa Spin.Beta *.  f_two a m k l Spin.Alfa Spin.Beta +.
          h_two i j m a Spin.Alfa Spin.Beta *.  f_two m a k l Spin.Alfa Spin.Beta ) +.
        sum mos_cabs (fun b -> 
            h_two i j a b Spin.Alfa Spin.Beta *. f_two a b k l Spin.Alfa Spin.Beta 
        )
      )
    )

let m_2112_2Ha_2Fa =
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a ->
        h_two i n a n Spin.Alfa Spin.Alfa *. f_two a j k l Spin.Alfa Spin.Alfa +. 
        h_two j n a n Spin.Alfa Spin.Alfa *. f_two a i l k Spin.Alfa Spin.Alfa 
      )
    )
    
let m_2112_2Hb_2Fa =
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a ->
        h_two i n a n Spin.Alfa Spin.Beta *. f_two a j k l Spin.Alfa Spin.Alfa +.
        h_two j n a n Spin.Alfa Spin.Beta *. f_two a i l k Spin.Alfa Spin.Alfa 
      )
    )
    
let m_2112_2Ha_2Fb =
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a ->
        h_two i n a n Spin.Alfa Spin.Alfa *. f_two a j k l Spin.Alfa Spin.Beta +.
        h_two j n a n Spin.Alfa Spin.Beta *. f_two a i l k Spin.Alfa Spin.Beta )
    )
    
    
let m_2121_2Ha_2Fa =
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a ->
        h_two i j a l Spin.Alfa Spin.Alfa *. f_two a n k n Spin.Alfa Spin.Alfa +.
        h_two j i a k Spin.Alfa Spin.Alfa *. f_two a n l n Spin.Alfa Spin.Alfa 
      )
    )
    

let m_2121_2Hb_2Fa =
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a ->
        h_two i j a l Spin.Alfa Spin.Beta *. f_two a n k n Spin.Alfa Spin.Alfa +.
        h_two j i a k Spin.Alfa Spin.Beta *. f_two a n l n Spin.Alfa Spin.Beta 
      )
    )
    
let m_2121_2Ha_2Fb =
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a ->
        h_two i j a l Spin.Alfa Spin.Alfa *. f_two a n k n Spin.Alfa Spin.Beta +.
        h_two j i a k Spin.Alfa Spin.Alfa *. f_two a n l n Spin.Alfa Spin.Beta 
      )
    )
    

let m_2122_2Ha_2Fa_ij =
  let s = Spin.Alfa in
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a ->
           h_two i n a k s s  *.  f_two j a n l s s 
        +. h_two i n a l s s  *.  f_two j a k n s s 
        -. h_two j n a k s s  *.  f_two i a n l s s   
        -. h_two j n a l s s  *.  f_two i a k n s s
      )
    )
    
let m_2122_2Hb_2Fb_ij =
  let s, s' = Spin.(Alfa, Beta) in
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a ->
          h_two n i a k s  s  *.  f_two a j n l s  s'
       +. h_two n j a l s  s' *.  f_two i a k n s  s 
       -. h_two n j k a s  s' *.  f_two i a n l s  s'
    )
  )
    
let m_2122_2Hb_2Fb_ij2 =
  let s, s' = Spin.(Alfa, Beta) in
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a ->
      -. h_two i n a l s  s' *.  f_two a j k n s  s' +.
      (if n < j then
                  h_two i n k a s  s' *.  f_two j a l n s' s'
               +. h_two n j a l s' s' *.  f_two i a k n s  s'
       else 
               -. h_two i n k a s  s' *.  f_two j a n l s' s' 
               -. h_two j n a l s' s' *.  f_two i a k n s  s'
      )
    )
  )
    
let m_2122_2Ha_2Fa_ij2 =
  let s, s' = Spin.(Alfa, Beta) in
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a ->
         h_two i n k a s s' *.  f_two j a l n s s'
      +. h_two j n l a s s' *.  f_two i a k n s s'
      -. h_two i n l a s s' *.  f_two j a k n s s'
      -. h_two j n k a s s' *.  f_two i a l n s s'
      )
    ) 
    
let m_2122_2Ha_2Fa_nv =
  let s = Spin.Alfa in
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a -> h_two i j a n s  s  *.  f_two n a k l s  s ) ) 
    
    
    
let m_2122_2Hb_2Fb_nv =
  let s, s' = Spin.(Alfa, Beta) in
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a -> -. h_two i j a n s s'  *.  f_two a n k l s s' ) ) 
    
let m_2122_2Hb_2Fb_nv2 =
  let s, s' = Spin.(Alfa, Beta) in
  array_5_init mo_num mo_num mo_num mo_num mo_num (fun n i j k l ->
    sum mos_cabs (fun a -> -. h_two i j n a s s'  *.  f_two n a k l s s' ) ) 
    
    
    
let integral_value ki kj = 
    let i, j, k, l, s, s', phase =
          match Excitation.of_det ki kj with
          | Excitation.(Double (phase, { hole ; particle ; spin }, {hole=hole' ; particle=particle' ; spin=spin' })) ->
            hole, hole', particle, particle', spin, spin', phase
          | _ -> assert false
    in
    let mos_i, mos_i' =
       match s with
       | Spin.Alfa -> mos_a ki, mos_b ki
       | Spin.Beta -> mos_b ki, mos_a ki
    in
    
    let mos_j, mos_j' =
       match s with
       | Spin.Alfa -> mos_a kj, mos_b kj
       | Spin.Beta -> mos_b kj, mos_a kj
    in
    
    let mos_ij, mos_ij' =
      let alfa = 
        let i = Spindeterminant.bitstring @@ Determinant.alfa ki in
        let j = Spindeterminant.bitstring @@ Determinant.alfa kj in
        Bitstring.to_list (Bitstring.logand i j)
      in
      let beta  =  
        let i = Spindeterminant.bitstring @@ Determinant.beta ki in
        let j = Spindeterminant.bitstring @@ Determinant.beta kj in
        Bitstring.to_list (Bitstring.logand i j)
      in
      match s with
      | Spin.Alfa -> alfa, beta
      | Spin.Beta -> beta, alfa
    in
    
    let mos_novirt, mos_novirt' =
      let alfa = 
        let i = Spindeterminant.bitstring @@ Determinant.alfa ki in
        let j = Spindeterminant.bitstring @@ Determinant.alfa kj in
        Bitstring.to_list (Bitstring.logor i j)
      in
      let beta  = 
        let i = Spindeterminant.bitstring @@ Determinant.beta ki in
        let j = Spindeterminant.bitstring @@ Determinant.beta kj in
        Bitstring.to_list (Bitstring.logor i j)
      in
      match s with
      | Spin.Alfa -> alfa, beta
      | Spin.Beta -> beta, alfa
    in
    
    let result = 
       if s = s' then
         m_2112_1H_2Fa.{i,j,k,l} +. 
         sum mos_i      (fun n -> m_2112_2Ha_2Fa.{n,i,j,k,l} ) +.
         sum mos_i'     (fun n -> m_2112_2Hb_2Fa.{n,i,j,k,l} ) +.
         sum mos_j      (fun n -> m_2121_2Ha_2Fa.{n,i,j,k,l} ) +.
         sum mos_j'     (fun n -> m_2121_2Ha_2Fb.{n,i,j,k,l} ) +.
         sum mos_ij     (fun n -> m_2122_2Ha_2Fa_ij.{n,i,j,k,l} ) +. 
         sum mos_ij'    (fun n -> m_2122_2Ha_2Fa_ij2.{n,i,j,k,l} ) +. 
         sum mos_novirt (fun n -> m_2122_2Ha_2Fa_nv.{n,i,j,k,l} ) 
       else
         m_2112_1H_2Fb.{i,j,k,l} +. 
         sum mos_i      (fun n -> m_2112_2Ha_2Fb.{n,i,j,k,l} ) +.
         sum mos_i'     (fun n -> m_2112_2Ha_2Fb.{n,j,i,l,k} ) +.
         sum mos_j      (fun n -> m_2121_2Hb_2Fa.{n,i,j,k,l} ) +.
         sum mos_j'     (fun n -> m_2121_2Hb_2Fa.{n,j,i,l,k} ) +.
         sum mos_novirt'(fun n -> m_2122_2Hb_2Fb_nv.{n,i,j,k,l} ) +.
         sum mos_novirt (fun n -> m_2122_2Hb_2Fb_nv2.{n,i,j,k,l} )+.
         sum mos_ij     (fun n -> m_2122_2Hb_2Fb_ij.{n,i,j,k,l} ) +. 
         sum mos_ij'    (fun n -> m_2122_2Hb_2Fb_ij2.{n,i,j,k,l} ) 
     in

    match phase with
    | Phase.Pos -> result
    | Phase.Neg -> -. result
     
let _ = check 100  integral_value 2 

let ki = det_I.(7)
let kj = det_I.(89)

let _ = integral_value ki kj
let _ = 
    let alphas =  generate_alphas ki kj 2 
    in compute_HaaF ki alphas kj



val m_2112_1H_2Fa :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <abstr>


val m_2112_1H_2Fb :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <abstr>


val m_2112_2Ha_2Fa :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <abstr>


val m_2112_2Hb_2Fa :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <abstr>


val m_2112_2Ha_2Fb :
  (float, Bigarray.float64_elt, Bigarray.fortran_layout) Bigarray.Genarray.t =
  <abstr>


...

- : unit = ()


val ki : Determinant.t =
  phase:+1
  a:+1 +--++-----------------------------------------------------------
  b:+1 +++-------------------------------------------------------------



val kj : Determinant.t =
  phase:+1
  a:+1 +-+-+-----------------------------------------------------------
  b:+1 ++-+------------------------------------------------------------



- : float = 0.000896378780435275082


- : float = 0.000896378780435274107


# 4. 3

In [130]:
let integral_value ki kj = 
    let i, j, m, k, l, n, s1, s2, s3, phase =
          match Excitation.of_det ki kj with
          | Excitation.(Triple (phase,
              { hole=h1 ; particle=p1 ; spin=s1 },
              { hole=h2 ; particle=p2 ; spin=s2 },
              { hole=h3 ; particle=p3 ; spin=s3 }) )  -> h1, h2, h3, p1, p2, p3, s1, s2, s3, phase
          | _ -> assert false
    in

    let result = 
       let open Spin in 
       match s1, s2, s3 with
       | Alfa, Alfa, Alfa
       | Beta, Beta, Beta -> 
           sum mos_cabs (fun a -> 
                h_two i j a k s1 s2 *.  f_two m a l n s3 s3 
             +. h_two i j a n s1 s2 *.  f_two m a k l s3 s2 
             +. h_two i m a l s1 s3 *.  f_two j a k n s2 s3 
             +. h_two j m a k s2 s3 *.  f_two i a l n s1 s3 
             +. h_two j m a n s2 s3 *.  f_two i a k l s1 s2 
             -. h_two i j a l s1 s2 *.  f_two m a k n s3 s3 
             -. h_two i m a k s1 s3 *.  f_two j a l n s2 s3 
             -. h_two i m a n s1 s3 *.  f_two j a k l s2 s2 
             -. h_two j m a l s2 s3 *.  f_two i a k n s1 s3 )
       | Alfa, Alfa, Beta
       | Beta, Beta, Alfa -> 
           sum mos_cabs (fun a -> 
                h_two i j a l s1 s2 *.  f_two a m k n s1 s3
             +. h_two i m k a s1 s3 *.  f_two j a l n s2 s3
             +. h_two j m a n s2 s3 *.  f_two i a k l s1 s2 
             +. h_two j m l a s2 s3 *.  f_two i a k n s1 s3
             -. h_two i j a k s1 s2 *.  f_two a m l n s1 s3
             -. h_two i m a n s1 s3 *.  f_two j a k l s2 s2 
             -. h_two i m l a s1 s3 *.  f_two j a k n s2 s3
             -. h_two j m k a s2 s3 *.  f_two i a l n s1 s3
           ) 
       | Alfa, Beta, Beta
       | Beta, Alfa, Alfa -> 
           sum mos_cabs (fun a -> 
                h_two i j a l s1 s2 *.  f_two a m k n s1 s3 
             +. h_two i m a n s1 s3 *.  f_two a j k l s1 s2 
             +. h_two i m k a s1 s3 *.  f_two j a l n s2 s3 
             +. h_two j m a n s2 s3 *.  f_two i a k l s1 s2 
             -. h_two i j a n s1 s2 *.  f_two a m k l s1 s2 
             -. h_two i j k a s1 s2 *.  f_two m a l n s2 s3 
             -. h_two i m a l s1 s3 *.  f_two a j k n s1 s3 
             -. h_two j m a l s2 s3 *.  f_two i a k n s1 s3 
           ) 
       | Beta, Alfa, Beta
       | Alfa, Beta, Alfa ->  assert false (*TODO *)
    in
    match phase with
    | Phase.Pos -> result
    | Phase.Neg -> -. result
     

let _ = check 100 integral_value 3 

val integral_value : Determinant.t -> Determinant.t -> float = <fun>


Checking ... 
 -  10 %
 -  20 %
 -  30 %
 -  40 %
 -  50 %
 -  60 %
 -  70 %
 -  80 %
 -  90 %
 - 100 %
OK: (13, 52) | 6.122906e-04 6.122906e-04 | 3.252607e-19  |  cpu : 77.238524  0.119682


- : unit = ()


---------------------------

In [ ]:
let ki = det_I.(129)
let kj = det_I.(349)

let alpha_to_string alpha = 
   
      let exc0 = Array.init (aux_num+1) (fun _ -> [|"-";"-"|]) in
 
      let i, j, m, k, l, n,  s, s', s'',  phase =
          match Excitation.of_det ki kj with
          | Excitation.(Triple (phase,
              { hole ; particle ; spin },
              {hole=hole' ; particle=particle' ; spin=spin' }, 
              {hole=hole''; particle=particle''; spin=spin''}  )) ->
            hole, hole', hole'', particle, particle', particle'', spin, spin', spin'', phase
          | _ -> assert false
      in
      let spin = function
        | Spin.Alfa -> 0
        | _ -> 1
      in
        exc0.(i).(spin s  ) <- "i" 
      ; exc0.(j).(spin s' ) <- "j" 
      ; exc0.(k).(spin s  ) <- "k" 
      ; exc0.(l).(spin s' ) <- "l" 
      ; exc0.(m).(spin s'') <- "m" 
      ; exc0.(n).(spin s'') <- "n" 
      ;
      let s0, s0', s0'' = s, s', s'' in
    
      let i, j, k, l, s, s', p1 =
          match Excitation.of_det ki alpha with
          | Excitation.(Double (phase, { hole ; particle ; spin }, {hole=hole' ; particle=particle' ; spin=spin' })) ->
            hole, hole', particle, particle', spin, spin', phase
          | _ -> assert false
      in
      
      if exc0.(i).(spin s ) =  "-" then exc0.(i).(spin s ) <- "p";
      if exc0.(j).(spin s') =  "-" then exc0.(j).(spin s') <- "p";
      if exc0.(k).(spin s ) =  "-" then exc0.(k).(spin s ) <- if k > mo_num then "a" else "q";
      if exc0.(l).(spin s') =  "-" then exc0.(l).(spin s') <- if l > mo_num then "a" else "q";
      
      let string_h = 
          Printf.sprintf "h_two %s %s %s %s %s %s *.  " 
            exc0.(i).(spin s )
            exc0.(j).(spin s')
            exc0.(k).(spin s )
            exc0.(l).(spin s')
            (if s  = s0  then "s " else if s = s0'  then "s'"  else "s''")
            (if s' = s0' then "s'" else if s = s0'' then "s''" else "s"  )
      in 
      
      let i, j, k, l, s, s', p2 =
          match Excitation.of_det alpha kj with
          | Excitation.(Double (phase, { hole ; particle ; spin }, {hole=hole' ; particle=particle' ; spin=spin' })) ->
            hole, hole', particle, particle', spin, spin', phase
          | _ -> assert false
      in
      
      let string_f = 
          Printf.sprintf "f_two %s %s %s %s %s %s" 
            exc0.(i).(spin s )
            exc0.(j).(spin s')
            exc0.(k).(spin s )
            exc0.(l).(spin s')
            (if s  = s0  then "s " else if s = s0'  then "s'"  else "s''")
            (if s' = s0' then "s'" else if s = s0'' then "s''" else "s"  )
      in
        (*
        Format.printf "|I> -> |a> : %a | %s\n@." Excitation.pp (Excitation.of_det ki alpha) string_h ;
        Format.printf "|a> -> |J> : %a | %s\n@." Excitation.pp (Excitation.of_det alpha kj) string_f ;
        *)

    
        let sign = 
            if Phase.add p1 p2 = phase then "+." else "-."
        in
        sign ^ string_h ^ string_f
    

let alpha_debug alpha = 
   
      let i, j, k, l, s, s', p1 =
          match Excitation.of_det ki alpha with
          | Excitation.(Double (phase, { hole ; particle ; spin }, {hole=hole' ; particle=particle' ; spin=spin' })) ->
            hole, hole', particle, particle', spin, spin', phase
          | _ -> assert false
      in
      Printf.printf "%d %d %d %d " i j k l;
      
      let i, j, k, l, s, s', p2 =
          match Excitation.of_det alpha kj with
          | Excitation.(Double (phase, { hole ; particle ; spin }, {hole=hole' ; particle=particle' ; spin=spin' })) ->
            hole, hole', particle, particle', spin, spin', phase
          | _ -> assert false
      in
      (*
        Format.printf "|I> -> |a> : %a | \n@." Excitation.pp (Excitation.of_det ki alpha) ;
        Format.printf "|a> -> |J> : %a | \n@." Excitation.pp (Excitation.of_det alpha kj) ;
        *)
      Printf.printf "%d %d %d %d \n%!" i j k l

      
let strings = 
    Format.printf "|I> -> |J> : %a |\n@." Excitation.pp (Excitation.of_det ki kj) ;
    generate_alphas ki kj 3 1 2 2
    |> Array.of_list
    |> Array.mapi (fun kk alpha -> alpha_to_string alpha)
    |> Array.to_list
    |> List.sort_uniq compare
    |> Array.of_list

let _ = Array.iteri (fun i x -> Printf.printf "%d %s \n%!" i x) strings

let _ =
  let v =
    let alphas =
      generate_alphas ki kj 3 1 2 2
      (*
      |> List.filter (fun alpha ->
        let x =  alpha_to_string alpha in
           x = strings.(6)
        )
        *)
    in
    (*
    List.iter alpha_debug alphas ;
    Printf.printf "\n%!";
    *)
    compute_HaaF ki alphas kj 
  in
  let x = (integral_value ki kj) in
  Printf.printf "%20.8e %20.8e %20.8e\n%!" x v (v-. x)
